# 1.0 Introduction 

# 2.0 Authenticating with Twitter's API 

In [3]:
!pip install Twython

In [4]:
from twython import Twython, TwythonError

In [5]:
pip install decorator==5.0.9

Note: you may need to restart the kernel to use updated packages.


## 2.1 Enter app info and get auth URL 

In order to authenticate with Twitter, we'll provide the app details and ask for a one-time authorization URL to authenticate your user with this app.

Copy and paste the API key and secret from your Twitter app into a file named keys.txt. The first line is the API_KEY and the second line of the file is API_SECRET_KEY. For example, a template for the keys.txt:

In [ ]:
# %load keys.txt
GRvkTm3qkMOM8YjyNp3S6xLO4
YmHFrSSnC7D1qNUemiDbmtaMvF0saiFzyyW15erffxGCuQyiFg

In [7]:
# open the keys file
my_file = open("keys.txt", "r")

# read the raw data
content = my_file.read()

# split all lines by  newline character
API_KEY, API_SECRET_KEY = content.split("\n")

# close the file
my_file.close()

In [8]:
twitter = Twython(API_KEY, API_SECRET_KEY)

authentication_tokens = twitter.get_authentication_tokens()
print(authentication_tokens['auth_url'])

https://api.twitter.com/oauth/authenticate?oauth_token=QvTtYwAAAAABZBP-AAABfyl6Vjs


## 2.2 Authorized tokens 

In [9]:
# Replace the verifier with the pin number obtained with your web browser in the previous step
VERIFIER = '3657835'

twitter = Twython(API_KEY, API_SECRET_KEY,
                  authentication_tokens['oauth_token'],
                  authentication_tokens['oauth_token_secret'])

authorized_tokens = twitter.get_authorized_tokens(VERIFIER)

## 2.3 Use authorized tokens 

In [10]:
twitter = Twython(API_KEY, API_SECRET_KEY,
                  authorized_tokens['oauth_token'],
                  authorized_tokens['oauth_token_secret'])

twitter.verify_credentials()

{'id': 1486095105811484677,
 'id_str': '1486095105811484677',
 'name': 'Renato Farias',
 'screen_name': 'renatolinsfar',
 'location': '',
 'description': '',
 'url': None,
 'entities': {'description': {'urls': []}},
 'protected': False,
 'followers_count': 9,
 'friends_count': 50,
 'listed_count': 6,
 'created_at': 'Tue Jan 25 21:55:10 +0000 2022',
 'favourites_count': 0,
 'utc_offset': None,
 'time_zone': None,
 'geo_enabled': False,
 'verified': False,
 'statuses_count': 2,
 'lang': None,
 'status': {'created_at': 'Sat Feb 19 02:16:57 +0000 2022',
  'id': 1494858513847312387,
  'id_str': '1494858513847312387',
  'text': 'Olá, você é um fã da #NFL ? Assistiu o último #SuperBowl ? Ou até mesmo gostaria de começar a acompanhar os jogos d… https://t.co/xR4LvMuHVL',
  'truncated': True,
  'entities': {'hashtags': [{'text': 'NFL', 'indices': [21, 25]},
    {'text': 'SuperBowl', 'indices': [46, 56]}],
   'symbols': [],
   'user_mentions': [],
   'urls': [{'url': 'https://t.co/xR4LvMuHVL',
 

# 5.0 Creating Twitter mention network

- Aqui começa a análise dos dados coletados. 

- A rede será criada de acordo com os steets que possuem o conteúdo "NFL".

## 5.1 Get some tweets

- Limit API

In [45]:
twitter.get_application_rate_limit_status()['resources']['search']

{'/search/tweets': {'limit': 180, 'remaining': 180, 'reset': 1645679793}}

- Para extrapolar o uso da API, iremos usar a função "sleep", para usar as 180 requisições a cada 15 minutos, extraindo assim o máximo de tweets em um curto intervalo de tempo.

In [49]:
import itertools
import time 

NUM_TWEETS_TO_FETCH = 17900
limit = 0

while limit < 1:
    cursor = twitter.cursor(twitter.search, q='Ukraine', count=100, result_type='mixed')
    search_tweets += list(itertools.islice(cursor, NUM_TWEETS_TO_FETCH))
    limit += 1
    time.sleep(910) #Dormir por 15 minutos
    
len(search_tweets)

54279

In [30]:
search_tweets

[{'created_at': 'Thu Feb 24 01:18:22 +0000 2022',
  'id': 1496655711106969607,
  'id_str': '1496655711106969607',
  'text': 'A Guerra na Ucrânia é a cada minuto mais eminente. As autoridades Ucranianas já recrutaram todos os seus reservista… https://t.co/Sr8rMdKbQP',
  'truncated': True,
  'entities': {'hashtags': [],
   'symbols': [],
   'user_mentions': [],
   'urls': [{'url': 'https://t.co/Sr8rMdKbQP',
     'expanded_url': 'https://twitter.com/i/web/status/1496655711106969607',
     'display_url': 'twitter.com/i/web/status/1…',
     'indices': [117, 140]}]},
  'metadata': {'iso_language_code': 'pt', 'result_type': 'recent'},
  'source': '<a href="http://twitter.com/download/android" rel="nofollow">Twitter for Android</a>',
  'in_reply_to_status_id': None,
  'in_reply_to_status_id_str': None,
  'in_reply_to_user_id': None,
  'in_reply_to_user_id_str': None,
  'in_reply_to_screen_name': None,
  'user': {'id': 68424764,
   'id_str': '68424764',
   'name': 'Danillo Amorim',
   'screen_n

In [48]:
len(search_tweets)

36379

- Aqui os tweets estão em formato de lista. 

- Na célula abaixo, iremos filtra apenas os itens que nos interessa, e transforma a lista em um dataframe pandas.

In [54]:
import pandas as pd

# Search tweets
dict_ = {'user': [], 'date': [], 'text': [], 'location':[], 'favorite_count': []}
for tweet in search_tweets:
    dict_['user'].append(tweet['user']['screen_name'])
    dict_['date'].append(tweet['created_at'])
    dict_['text'].append(tweet['text'])
    dict_['location'].append(tweet['user']['location'])
    dict_['favorite_count'].append(tweet['favorite_count'])
# Structure data in a pandas DataFrame for easier manipulation
df = pd.DataFrame(dict_)

In [55]:
df.shape

(54279, 5)

## 5.2 Baixando o Dataset 

- Fazendo o download do dataset por dia. 

In [33]:
df

user                            date  \
0        nilloamorim  Thu Feb 24 01:18:22 +0000 2022   
1    ahmetmuhtar1917  Wed Feb 23 18:19:31 +0000 2022   
2     mahmuteksi1917  Wed Feb 23 18:18:34 +0000 2022   
3         Renascenca  Wed Feb 23 17:20:32 +0000 2022   
4       _eswa_sultan  Wed Feb 23 12:25:08 +0000 2022   
..               ...                             ...   
574       Drdicastro  Thu Feb 17 15:23:20 +0000 2022   
575  InvestingBrasil  Thu Feb 17 14:57:00 +0000 2022   
576     Tarmizi_Muji  Thu Feb 17 13:59:44 +0000 2022   
577        thework05  Wed Feb 16 22:20:02 +0000 2022   
578        luzdanet8  Wed Feb 16 18:01:25 +0000 2022   

                                                  text  \
0    A Guerra na Ucrânia é a cada minuto mais emine...   
1    RT @lghkoor: Emperyalist çıkarlar için açılan ...   
2    RT @lghkoor: Emperyalist çıkarlar için açılan ...   
3    Marcelo elogia intervenção do Papa no conflito...   
4    RT @Alihira_nur: 12 adaları verip kurtulduk di...   
..                                                 ...   
574  RT @InvestingBrasil: Mercado tenso com troca d...   
575  Mercado tenso com troca de acusações na crise ...   
576  WW3 you can only predict but Muhammad Qasim wa...   
577  Sobre a tensão #RussiaUcrânia  : não dá para e...   
578  "Rússia-Ucrânia: Por que o mercado não confia ...   

                        location  favorite_count  
0              Saquarema, Brasil               0  
1                                              0  
2                                              0  
3                                              0  
4                                              0  
..                           ...             ...  
574                                            0  
575                                            3  
576  Denpasar Selatan, Indonesia               0  
577                                            0  
578       Rio de Janeiro, Brasil               0  

[579 rows x 5 columns]

## 5.3 Creating DiGraph 
It's not necessary to first filter out tweets containing user mentions due to a feature of Tweet Objects: every tweet has Entities which always contains a 'user_mentions' list, even if that list is empty. Since a tweet may mention more than one user, we need a nested for-loop.

In [50]:
import networkx as nx

D = nx.DiGraph()

for tweet in search_tweets:
    tweet_sn = tweet['user']['screen_name']
    for user_mention in tweet['entities']['user_mentions']:
        mentioned_sn = user_mention['screen_name']
        
        my_edge = (tweet_sn, mentioned_sn)
        if D.has_edge(*my_edge):
            D.edges[my_edge]['weight'] += 1
        else:
            D.add_edge(*my_edge, weight=1)

# 5.4 Analyze graph

## 5.4.1 Most popular users

In [51]:
max(D.nodes, key=D.in_degree)

'UNGeneva'

In [52]:
from operator import itemgetter

sorted(D.in_degree(), key=itemgetter(1), reverse=True)[:5]

[('UNGeneva', 643),
 ('ARanganathan72', 641),
 ('WalshFreedom', 311),
 ('MattWalshBlog', 250),
 ('CBSNews', 235)]

## 5.4.2 Conversation drivers

In [53]:
sorted(D.out_degree(weight='weight'), key=itemgetter(1), reverse=True)[:5]

[('cosmicblast17', 99),
 ('GusevOAl', 84),
 ('2kbb', 81),
 ('Bob_Stinson1234', 66),
 ('ZaleskiLuke', 60)]

## 5.4.3 Connectivity

In [300]:
nx.is_weakly_connected(D)

False

In [301]:
nx.number_weakly_connected_components(D)

3128

## 5.4.4 Locations with the most  NFL Tweets

In [362]:
freq = dftotal.groupby(['location'])["user"].count() 

In [363]:
type(freq)

pandas.core.series.Series

In [364]:
freq = freq.sort_values(ascending = False)

In [367]:
freq[:35]

location
                     220740
United States          9130
Los Angeles, CA        5293
Boise, ID              2991
Chicago, IL            2945
California, USA        2756
USA                    2588
Houston, TX            2352
Florida, USA           2324
Atlanta, GA            2275
New York, NY           2101
Texas, USA             2100
Dallas, TX             2091
Washington, DC         1954
New York, USA          1865
New Jersey, USA        1716
México                 1708
Cincinnati, OH         1657
Las Vegas, NV          1549
Pittsburgh, PA         1541
Philadelphia, PA       1407
Ohio, USA              1341
Seattle, WA            1314
Boston, MA             1256
Maryland, USA          1195
Miami, FL              1192
Pennsylvania, USA      1174
Brasil                 1155
Baltimore, MD          1145
Michigan, USA          1143
Los Angeles            1136
Indianapolis, IN       1133
New York               1129
Earth                  1125
London, England        1108
Name: user,

In [56]:
df.nlargest(30, 'favorite_count')[['user','favorite_count']]

user  favorite_count
36379         Ukraine          364346
18479           POTUS           83139
18480    DmytroKuleba           81300
579             POTUS           79438
580      DmytroKuleba           76569
51418  ARanganathan72           28815
33550  ARanganathan72           27769
15655  ARanganathan72           27506
36381         BNONews           15443
39049  DonaldJTrumpJr           14276
21151  DonaldJTrumpJr           14038
3251   DonaldJTrumpJr           13992
47259       lapatina_           11469
29381       lapatina_           11056
11484       lapatina_           10912
38369     MattZeitlin            9559
20470     MattZeitlin            8474
36380    olgatokariuk            8151
2570      MattZeitlin            8150
50803     ElectionWiz            5103
32934     ElectionWiz            5031
15039     ElectionWiz            5005
18481    olgatokariuk            3731
581      olgatokariuk            3306
54142      Kasparov63            1746
36282      Kasparov63            1726
18387      Kasparov63            1718
47831   NaveedAJamali            1441
29955   NaveedAJamali            1431
12058   NaveedAJamali            1430